![header](../figures/logos_partenaires_DC_WOC-ESA.jpg)

# Mediterranean: Benchmark DUACS all sat (cmems L4 products) plot maps
 

***
**Authors:** Datlas <br>
**Copyright:** 2023 Datlas <br>
**License:** MIT

<div class="alert alert-block alert-success">
<h1><center> Mediterranean: Benchmark of DUACS all sat plot maps</center></h1>
<h4><center> The notebook aims to plot maps produced by the DUACS all sat (cmems L4 products) system in the Mediterranean region. </center></h4> 
</div>

In [3]:
from glob import glob
import numpy as np
import os

In [4]:
import sys
sys.path.append('..')
from src.mod_plot import *
from src.mod_stat import *
from src.mod_spectral import *
from src.mod_interp import *
from src.mod_switchvar import *

In [5]:
import logging
logger = logging.getLogger()
logger.setLevel(logging.INFO)

<div class="alert alert-info" role="alert">

<h2>0. Parameters</h2>

</div>

In [6]:
time_min = '2019-01-15'                                        # time min for analysis
time_max = '2019-12-15'                                        # time max for analysis 

method_name = 'DUACS_allsat'

# Region details
region = 'Mediterranean'
lon_min = 355                                          # domain min longitude
lon_max = 25                                          # domain max longitude
lat_min = 35.                                          # domain min latitude
lat_max = 47.                                          # domain max latitude

output_dir = '../results/'+method_name+'/'                                      # output directory path
os.system(f'mkdir -p {output_dir}')

figures_dir = '../figures/'+method_name+'/'                                      # figures directory path
os.system(f'mkdir -p {figures_dir}')

box_lonlat = {'lon_min':lon_min,'lon_max':lon_max,'lat_min':lat_min,'lat_max':lat_max}




<div class="alert alert-info" role="alert">

<h2>1. Input files</h2>

</div>

## Sea Surface Height maps to evaluate

In [7]:
%%time
list_of_maps = sorted(glob('../data/maps/cmems_obs-sl_glo_phy-ssh_my_allsat-l4-duacs-0.25deg_P1D_WOC-'+region+'.nc'))
ds_maps = xr.open_mfdataset(list_of_maps, combine='nested', concat_dim='time')
ds_maps = ds_maps.sel(time=slice(time_min, time_max))
ds_maps

CPU times: user 39.2 ms, sys: 23.5 ms, total: 62.6 ms
Wall time: 131 ms


<xarray.Dataset>
Dimensions:    (time: 335, latitude: 49, longitude: 121)
Coordinates:
  * latitude   (latitude) float32 34.88 35.12 35.38 35.62 ... 46.38 46.62 46.88
  * time       (time) datetime64[ns] 2019-01-15 2019-01-16 ... 2019-12-15
  * longitude  (longitude) float32 -5.125 -4.875 -4.625 ... 24.38 24.62 24.88
Data variables:
    adt        (time, latitude, longitude) float64 dask.array<chunksize=(335, 49, 121), meta=np.ndarray>
    ugos       (time, latitude, longitude) float64 dask.array<chunksize=(335, 49, 121), meta=np.ndarray>
    vgos       (time, latitude, longitude) float64 dask.array<chunksize=(335, 49, 121), meta=np.ndarray>
    crs        (time) int32 -2147483647 -2147483647 ... -2147483647 -2147483647
    sla        (time, latitude, longitude) float64 dask.array<chunksize=(335, 49, 121), meta=np.ndarray>
Attributes: (12/45)
    Conventions:                                    CF-1.6
    FROM_ORIGINAL_FILE__Metadata_Conventions:       Unidata Dataset Discovery...
    cdm_data_type:                                  Grid
    comment:                                        Sea Surface Height measur...
    contact:                                        servicedesk.cmems@mercato...
    creator_email:                                  servicedesk.cmems@mercato...
    ...                                             ...
    time_coverage_duration:                         P1D
    time_coverage_end:                              2023-06-07T12:00:00Z
    time_coverage_resolution:                       P1D
    time_coverage_start:                            2023-06-06T12:00:00Z
    title:                                          DT merged all satellites ...
    _CoordSysBuilder:                               ucar.nc2.dataset.conv.CF1...

## Plot DUACS geostrophic currents movie

In [ ]:
movie(ds_maps,name_var='uv', method=method_name, region=region, dir_output=output_dir,dim_name=['time','latitude','longitude'],
          framerate=24,Display=True,clim=[0,1.2],cmap='YlGnBu_r', newmovie=True, figsize=(12,6))


## Compute and plot DUACS relative vorticity movie

In [7]:
rv = currents_to_relative_vorticity(np.array(ds_maps.ugos),np.array(ds_maps.vgos), ds_maps.longitude,ds_maps.latitude)

ds_maps = ds_maps.assign(rv=lambda ds_maps: ds_maps.sla * 0 + rv)

In [8]:
movie(ds_maps,name_var='rv', method=method_name, region=region, dir_output=output_dir,dim_name=['time','latitude','longitude'],
          framerate=24,Display=True,clim=[-0.8,0.8],cmap='RdBu_r', newmovie=True, figsize=(12,6))
